# Manejo de coordenadas y su complejidad

Las coordenadas x, y de cada registro son las características con las cuales el sistema de información ArcGis se alimenta para permitir la visualización. La problemática principal asociada al dataset es, precisamente, errores cometidos durante el proceso de caracterización que afectan las coordenadas que afectan aproximadamente a un ***xxxxx*** de los registros, posicionándolos fuera de antioquia o guardándolos todos en un lugar específico.

Las coordenadas son registradas en el dataset a partir del lugar geográfico en el que fue completada la encuesta, por lo cual, si múltiples personas por ejemplo a la sede de la alcaldía del municipio para ser encuestadas, sus coordenadas temrinarán representando un clúster alrededor de la sede de la alcaldía en el casco urbano del municipio. Otro factor que interviene es la conexión a internet al momento de completar la encuesta: si al enviarla no hay conexión a internet, la información periste hasta que el dispositivo tenga conexión; esto en ocasiones hace que se guarden coordenadas fuera de antioquia.

Por esto, la corrección de coordenadas es crucial para una correcta caracterización y diagnóstico de la inclusión a nivel de Población con Discapacidad e Inclusión en el departamento de Antioquia.

A continuación, el plan para abordar esta problemática:



## Detección de coordenadas erróneas

Con el fin de identificar las coordenadas erróneas, es necesario comparar el resultado de la búsqueda con ArcGis con la vereda o el barrio registrado en el dataset.

A través de la API de ArcGis se pueden consultar las veredas con su nombre completo, sin embargo, en el dataset es común encontrarlas con el nombre modificado, incompleto o faltante. Algunos ejemplos que se pueden encontrar en el dataset en la columna "Nombre del Barrio o Vereda (PcD)" son:

- "concepcio" (nombre incompleto)
- "Calle santander 19" (No es el nombre de un barrio o una vereda, es una calle)
- "La pava" (Nombre correcto)

En vista de que debemos comparar y encontrar similitudes entre la vereda o barrio registrado en el dataset y el registrado en ArcGis, es necesario un *Procesamiento de nombres de Barrios y Veredas*, dividido en diferentes fases.



In [1]:
!pip install unidecode
!pip install arcgis
!pip install rapidfuzz

In [2]:
# Normalización de nombres de municipios, barrios y veredas en la versión limpia del dataset original

from normalizar_texto import agregar_columnas_normalizadas

file_path = "clean_pcd_data.csv"

# Llamar al método y almacenar el resultado
dataset_actualizado = agregar_columnas_normalizadas(file_path)

# Verificar las nuevas columnas
print(dataset_actualizado[["Municipio_normalizado", "BarrioVereda_normalizado"]].head())


  Municipio_normalizado BarrioVereda_normalizado
0             abejorral                    tejar
1             abejorral                    tejar
2             abejorral                    tejar
3             abejorral                     pena
4             abejorral                esperanza


Habiendo normalizado los nombres de las veredas y municipios, el procesamiento de texto se hace mucho más sencillo. A continuación, se evalúan cuáles registros de la columna "Zona de residencia (PcD)" corresponden a la Zona Rural de su municipio y cuáles a la Zona Urbana. Esto porque la Zona Urbana en lugar de estar dividida en veredas, está dividida en barrios, y dichos barrios (así como zonas descritas a partir de nombres de calles o direcciones) no se encuentran disponibles en los mapas de ArcGis para todos los municipios. El procesamiento de direcciones y barrios de las zonas urbanas está destinado para entregas futuras.

In [3]:
import coordenadas_arcgis as ag 

df_urbano, df_rural = ag.dividir_por_zona(dataset_actualizado)

## Procesamiento de coordenadas en la zona rural

### Obtención de coordenadas de las veredas

In [ ]:
import normalizar_texto as norm
import coincidencia_difusa as cd


def procesar_coordenadas_vereda(row):
    
    vereda_dataset = row["Nombre del Barrio o Vereda (PcD)"]

    # Tomar las coordenadas y verificar si están en la vereda
    x = row["x"]
    y = row["y"]
    vereda = ag.query_vereda(x, y)

    # No se encontró una vereda asociada a esas coordenadas
    if vereda == None:
        # Buscar coordenada de la vereda registrada en el dataset
        print("No se encontró vereda")
        x, y = ag.query_vereda_coordinates(vereda_dataset)

        # Si no se encuentra, se ponen las coordenadas del municipio
        if x is None or y is None:
            # Poner la del municipio***
            id = row["ObjectID"]
            municipio = row["Municipio de residencia (PcD)"]
            row["x"], row["y"] = ag.geocode_municipio(municipio)
            print(f"No se pudo encontrar la vereda {vereda_dataset} del registro {id} en el mapa de veredas. /nAsignando coordenadas del municipio {municipio}.")
        
        else:
            print(f"Coordenadas encontradas para {vereda_dataset}: {x}, {y}")
            row["x"] = x
            row["y"] = y
    # Se encontró una vereda asociada a esas coordenadas
    else:

        # Normalización de la vereda obtenida desde ArcGis
        vereda_norm = norm.normalizar_texto(vereda)

        # Comparar vereda registrada en la encuesta y vereda obtenida en la consulta
        vereda_original = row["BarrioVereda_normalizado"]
        similitud = cd.comparar_frases(vereda_norm, vereda_original, 65)

        print(f"Existe similitud entre {vereda_original} y {vereda_norm}: {similitud}")

        # Si la similitud es menor al 65% se toma el nombre de la vereda registrada originalmente y se busca en el mapa de veredas
        if not similitud:
            x, y = ag.query_vereda_coordinates(vereda_dataset)
            
            # Se intenta encontrar la vereda del dataset en el mapa de veredas
            if x is None or y is None:
                # Poner las coordenadas del municipio
                municipio = row["Municipio de residencia (PcD)"]
                row["x"], row["y"] = ag.geocode_municipio(municipio)
                print(f"No se pudo encontrar la vereda {vereda_dataset} en el mapa de veredas. /nAsignando coordenadas del municipio {municipio}.")
            else:
                print(f"Coordenadas encontradas para {vereda_dataset}: {x}, {y}")
                row["x"] = x
                row["y"] = y
            
df_rural.apply(procesar_coordenadas_vereda, axis=1)

Existe similitud entre pena y pena: True
No se encontró vereda
Coordenadas encontradas para La esperanza: -75.03794019673747, 6.836805510555339
Existe similitud entre canaveral y chagual: False
Coordenadas encontradas para CAÑAVERAL: -75.83552359997167, 5.655938344035428
Existe similitud entre chagualal y chagual: True
Existe similitud entre canaveral y chagual: False
Coordenadas encontradas para CAÑAVERAL: -75.83552359997167, 5.655938344035428
Existe similitud entre chagualal y chagual: True
Existe similitud entre granadillo y granadillo: True
Existe similitud entre granadillo y granadillo: True
No se encontró vereda
Coordenadas encontradas para BUEY COLMENAS: -75.42129290003527, 5.899200756759565
Existe similitud entre pantanillo y montel oro reposo: False
Coordenadas encontradas para Pantanillo: -74.97314287207564, 6.645763961370728
Existe similitud entre vocan y volcan: True
Existe similitud entre monteloro y montel oro reposo: True
Existe similitud entre naranjal y polka: False
Co

## Procesamiento de coordenadas en la zona urbana

### Verificación de coordenadas

Debido a las limitaciones en el alcance del presente entregable, se tomó la decisión de verificar únicamente, en el caso de las coordenadas pertenecientes a un registro en una Zona Urbana, si las coordenadas presentes registradas estaban dentro del municipio correspondiente. En caso contrario, se le asignan las coordenadas por defecto del municipio.

In [ ]:

def asignar_municipio(municipio):
    new_x, new_y = ag.geocode_municipio(municipio)
    print(f"Nuevas coordenadas: {new_x}, {new_y}")
    return new_x, new_y


def procesar_coordenadas_municipio(row):

    # Saber si las coordenadas registradas hacen parte de algún municipio y cuál
    x = row["x"]
    y = row["y"]
    municipio = ag.reverse_geocode_municipio(x, y)
    if municipio == None:
        print(f"No se encontró el municipio en las coordenadas x, y: {x}, {y}")
        municipio = row["Municipio de residencia (PcD)"]
        row["x"], row["y"] = asignar_municipio(municipio)
    else:
        # Normalizar nombre del municipio
        municipio = str(municipio)
        municipio_arcgis = norm.normalizar_texto(municipio)

        # Comparar nombre normalizado del municipio (Se consideran válidas si coinciden al menos en un 70%)
        municipio_onal_norm = row["Municipio_normalizado"] # Municipio original pero normalizado
        similitud = cd.comparar_frases(municipio_arcgis, municipio_onal_norm, 70)
        

        # Si la similitud entre el municipio que marcan las coordenadas y el del dataset es menor al 70%, se ponen las coordenadas del municipio original
        if not similitud:
            print(f"Similitud entre {municipio_onal_norm} y {municipio_arcgis}: {similitud}")
            municipio = row["Municipio de residencia (PcD)"]
            row["x"], row["y"] = asignar_municipio(municipio)


df_urbano.apply(procesar_coordenadas_municipio, axis=1)

Reverse geocoding coordinates: -75.43145363, 5.789384265
Reverse Geocode Result: {'address': {'Match_addr': 'Rios Gonzalez Hernan De Jesus', 'LongLabel': 'Rios Gonzalez Hernan De Jesus, Calle 52 49 47, Abejorral, Antioquia, COL', 'ShortLabel': 'Rios Gonzalez Hernan De Jesus', 'Addr_type': 'POI', 'Type': 'Restaurant', 'PlaceName': 'Rios Gonzalez Hernan De Jesus', 'AddNum': '49 47', 'Address': 'Calle 52 49 47', 'Block': '', 'Sector': '', 'Neighborhood': '', 'District': '', 'City': 'Abejorral', 'MetroArea': '', 'Subregion': 'Abejorral', 'Region': 'Antioquia', 'RegionAbbr': 'ANT', 'Territory': '', 'Postal': '055030', 'PostalExt': '', 'CntryName': 'Colombia', 'CountryCode': 'COL', 'X': -75.431490635501, 'Y': 5.789298269312, 'InputX': -75.43145363, 'InputY': 5.789384265}, 'location': {'x': -75.431490635501, 'y': 5.789298269312, 'spatialReference': {'wkid': 4326, 'latestWkid': 4326}}}
Found municipio: Abejorral
Reverse geocoding coordinates: -75.43099612, 5.789354334
Reverse Geocode Result: {

## Unificación de datasets